OData API

https://oda.ft.dk/Home/OdataQuery

https://www.odata.org/

https://www.ft.dk/-/media/sites/ft/pdf/dokumenter/aabne-data/oda-browser_brugervejledning.ashx

https://www.odata.org/documentation/odata-version-3-0/url-conventions/

https://www.odata.org/documentation/odata-version-3-0/odata-version-3-0-core-protocol/

Source root Link: "https://oda.ft.dk/api/"

ftp://oda.ft.dk/ODAXML/Referat/samling/


In [84]:
import requests
import urllib.request
import os
import io
import json

import numpy as np
import pandas as pd
from sklearn.decomposition import NMF
from sklearn.feature_extraction.text import TfidfVectorizer

from bs4 import BeautifulSoup as bs
from bs4.element import Comment
import lxml

import xml.etree.ElementTree as et 
from xml.dom import minidom

import re

In [85]:
#pip install bs4 lxml

In [90]:
path = os.getcwd()

In [91]:
path

'/Users/frederikkromannhansen/Library/Mobile Documents/com~apple~CloudDocs/.Trash/Referater - 20091_M3'

In [ ]:
#paths = ['data/EdixiXMLExport_20091.xml','data/EdixiXMLExport_20101.xml',
#         'data/EdixiXMLExport_20102.xml','data/EdixiXMLExport_20111.xml',
#         'data/EdixiXMLExport_20121.xml','data/EdixiXMLExport_20131.xml',
#         'data/EdixiXMLExport_20142.xml',
#         'data/EdixiXMLExport_20151.xml','data/EdixiXMLExport_20161.xml']


#paths =['data/EdixiXMLExport_20141.xml']
#for path in paths:
tree = et.parse(path)
#root=tree
root = tree.getroot() 


starttid_vec = []
sluttid_vec=[]
navn_vec = []
efternavn_vec = []
tekst_vec = []
parti_vec = []
rolle_vec = []

for speech in root.iter('Tale'):
    tags=[node.tag for node in speech.iter()]
    if('TekstGruppe' in tags):
        if('GroupNameShort' in tags):
            for node in speech.iter():
                if(node.tag == 'StartDateTime'):
                    starttid_vec.append(node.text)
                elif(node.tag == 'OratorFirstName'):
                    navn_vec.append(node.text)
                elif(node.tag == 'OratorLastName'):
                    efternavn_vec.append(node.text)
                elif(node.tag == 'OratorRole'):
                    rolle_vec.append(node.text)
                elif(node.tag=='TekstGruppe'):
                    tekstgruppe = ''
                    for k in node.iter():
                        if k.tag=="Char":
                            tekstgruppe+=' '+k.text
                    tekst_vec.append(tekstgruppe)
                elif(node.tag=='GroupNameShort'):
                    parti_vec.append(node.text)
                
                if len(tekst_vec)>len(navn_vec):
                    tekst_vec.pop()
                if len(starttid_vec)>len(navn_vec):
                    starttid_vec.pop()

        else:
            parti_vec.append('Ukendt')
            for node in speech.iter():
                if(node.tag == 'StartDateTime'):
                    starttid_vec.append(node.text)
                elif(node.tag == 'OratorFirstName'):
                    navn_vec.append(node.text)
                elif(node.tag == 'OratorLastName'):
                    efternavn_vec.append(node.text)
                elif(node.tag == 'OratorRole'):
                    rolle_vec.append(node.text)
                elif(node.tag=='TekstGruppe'):
                    tekstgruppe = ''
                    for k in node.iter():
                        if k.tag=="Char":
                            tekstgruppe+=' '+k.text
                    tekst_vec.append(tekstgruppe)
                if len(tekst_vec)>len(navn_vec):
                    tekst_vec.pop()
                if len(starttid_vec)>len(navn_vec):
                    starttid_vec.pop()

dictionary= {'StartDateTime':starttid_vec,'OratorFirstName':navn_vec,'OratorLastName':efternavn_vec,
                 'GroupNameShort':parti_vec,'OratorRole':rolle_vec ,'TekstGruppe':tekst_vec} # 'EndDateTime':sluttid_vec,

df = pd.DataFrame(dictionary)
#df.to_csv(path[0:26]+'csv')

In [56]:
referater = []
#pd.DataFrame()
i=0
for _, _, files in os.walk(path):
        for file in files:
#            while i < 1:
                if file.endswith('20091_M100_helemoedet.xml'):
                    print(file)
                    #text = io.open(path+file,'rt',encoding = 'utf-8').read()
                    with open(path+file, "r") as referat:
                        content = referat.read()
                        referater += bs(content, "lxml")
                        bs(content, "lxml")
        
                        i += 1

20091_M100_helemoedet.xml


In [65]:
referater = []
#pd.DataFrame()
i=0
for _, _, files in os.walk(path):
        for file in files:
#            while i < 1:
                if file.endswith('.xml'):
                    print(file)
                    #text = io.open(path+file,'rt',encoding = 'utf-8').read()
                    with open(path+file, "r") as referat:
                        content = referat.read()
                        referater += bs(content, "lxml")
                        bs(content, "lxml")
        
                        i += 1

In [66]:
bs(content,'lxml')

<html><body><p>﻿<?xml version="1.0" encoding="utf-8"?><dokument edixistatus=""><metameeting><parliamentarysession>20091</parliamentarysession><parliamentarygroup>Folketinget</parliamentarygroup><meetingnumber>100</meetingnumber><dateofsitting>2010-05-31T10:00:00</dateofsitting><location>Folketingssalen</location><edixidoclocation>W:\20091\M100\</edixidoclocation><audiofilefolder>X:\DAudio\FT2009\100\SALEN\</audiofilefolder></metameeting><titelgruppe><titel><linea><char>100. møde</char></linea></titel><undertitel><linea><char>Mandag den 31. maj 2010 kl. 10.00</char></linea></undertitel></titelgruppe><dagsordenplan><rubrica>
<linea>
<char>Dagsorden</char>
</linea>
</rubrica>
<punkttekst>
<exitus>
<linea>
<char>1) 1. behandling af lovforslag nr. L 222:</char>
</linea>
</exitus>
<exitus>
<linea>
<char>Forslag til lov om ændring af lov om arbejdsløshedsforsikring m.v. (Nedsættelse af dagpengeperioden).</char>
</linea>
</exitus>
<exitus>
<linea>
<char>Af beskæftigelsesministeren (Inger Støjb

In [70]:
result=re.search('<char>Atf\W+<char>Af',content)

In [75]:
re.search('<char>Af(*)<char>Af',content)

error: nothing to repeat at position 9

In [73]:
print(result)

None


In [71]:
print(result.group(1))

AttributeError: 'NoneType' object has no attribute 'group'

In [55]:
bs(referater[0],'lxml')

TypeError: 'NoneType' object is not callable

In [50]:
pd.Series(referater)

0    [[[﻿, xml version="1.0" encoding="utf-8"?, <do...
dtype: object

In [51]:
referater[0]

<html><body><p>﻿<?xml version="1.0" encoding="utf-8"?><dokument edixistatus=""><metameeting><parliamentarysession>20091</parliamentarysession><parliamentarygroup>Folketinget</parliamentarygroup><meetingnumber>100</meetingnumber><dateofsitting>2010-05-31T10:00:00</dateofsitting><location>Folketingssalen</location><edixidoclocation>W:\20091\M100\</edixidoclocation><audiofilefolder>X:\DAudio\FT2009\100\SALEN\</audiofilefolder></metameeting><titelgruppe><titel><linea><char>100. møde</char></linea></titel><undertitel><linea><char>Mandag den 31. maj 2010 kl. 10.00</char></linea></undertitel></titelgruppe><dagsordenplan><rubrica>
<linea>
<char>Dagsorden</char>
</linea>
</rubrica>
<punkttekst>
<exitus>
<linea>
<char>1) 1. behandling af lovforslag nr. L 222:</char>
</linea>
</exitus>
<exitus>
<linea>
<char>Forslag til lov om ændring af lov om arbejdsløshedsforsikring m.v. (Nedsættelse af dagpengeperioden).</char>
</linea>
</exitus>
<exitus>
<linea>
<char>Af beskæftigelsesministeren (Inger Støjb

In [53]:
print(referater[0].findAll('char'))

[<char>100. møde</char>, <char>Mandag den 31. maj 2010 kl. 10.00</char>, <char>Dagsorden</char>, <char>1) 1. behandling af lovforslag nr. L 222:</char>, <char>Forslag til lov om ændring af lov om arbejdsløshedsforsikring m.v. (Nedsættelse af dagpengeperioden).</char>, <char>Af beskæftigelsesministeren (Inger Støjberg).</char>, <char>(Fremsættelse 27.05.2010).</char>, <char>2) 1. behandling af lovforslag nr. L 218:</char>, <char>Forslag til lov om ændring af lov om nedsættelse af statstilskuddet til kommuner ved forhøjelser af den kommunale skatteudskrivning. (Ændring af perioden for individuelle nedsættelser af bloktilskuddet og justering af undtagelsesbestemmelserne for kommuner, der tidligere har nedsat skatten).</char>, <char>Af indenrigs- og sundhedsministeren (Bertel Haarder).</char>, <char>(Fremsættelse 26.05.2010).</char>, <char>3) 1. behandling af lovforslag nr. L 219:</char>, <char>Forslag til lov om ændring af lov om kommunal udligning og generelle tilskud til kommuner. (Forh

In [54]:
referater[0].findAll('char')

[<char>100. møde</char>,
 <char>Mandag den 31. maj 2010 kl. 10.00</char>,
 <char>Dagsorden</char>,
 <char>1) 1. behandling af lovforslag nr. L 222:</char>,
 <char>Forslag til lov om ændring af lov om arbejdsløshedsforsikring m.v. (Nedsættelse af dagpengeperioden).</char>,
 <char>Af beskæftigelsesministeren (Inger Støjberg).</char>,
 <char>(Fremsættelse 27.05.2010).</char>,
 <char>2) 1. behandling af lovforslag nr. L 218:</char>,
 <char>Forslag til lov om ændring af lov om nedsættelse af statstilskuddet til kommuner ved forhøjelser af den kommunale skatteudskrivning. (Ændring af perioden for individuelle nedsættelser af bloktilskuddet og justering af undtagelsesbestemmelserne for kommuner, der tidligere har nedsat skatten).</char>,
 <char>Af indenrigs- og sundhedsministeren (Bertel Haarder).</char>,
 <char>(Fremsættelse 26.05.2010).</char>,
 <char>3) 1. behandling af lovforslag nr. L 219:</char>,
 <char>Forslag til lov om ændring af lov om kommunal udligning og generelle tilskud til kom

In [46]:
url = 'ftp://oda.ft.dk/ODAXML/Referat/samling/20091/'
response = urllib.request.urlopen(url)
data = response.read()      # a `bytes` object
text = referater[0].find('char').decode('utf-8')

TypeError: unsupported operand type(s) for -: 'str' and 'int'

In [47]:
text

'\ufeff<?xml version="1.0" encoding="utf-8"?><Dokument edixistatus=""><MetaMeeting><ParliamentarySession>20091</ParliamentarySession><ParliamentaryGroup>Folketinget</ParliamentaryGroup><MeetingNumber>1</MeetingNumber><DateOfSitting>2009-10-06T12:00:00</DateOfSitting><Location>Folketingssalen</Location><EdixiDocLocation>W:\\20091\\M001\\</EdixiDocLocation><AudioFileFolder>X:\\DAudio\\FT2009\\001\\SALEN\\</AudioFileFolder></MetaMeeting><TitelGruppe><Titel><Linea><Char>1. møde</Char></Linea></Titel><UnderTitel><Linea><Char>Tirsdag den 6. oktober 2009 kl. 12.00</Char></Linea></UnderTitel></TitelGruppe><DagsordenPlan><Rubrica>\n  <Linea>\n    <Char>1. møde</Char>\n  </Linea>\n  <Linea>\n    <Char>Tirsdag den 6. oktober 2009 kl. 12.00</Char>\n  </Linea>\n</Rubrica>\n<PunktTekst>\n  <Exitus>\n    <Linea>\n      <Char>\n      </Char>\n    </Linea>\n  </Exitus>\n</PunktTekst></DagsordenPlan><DagsordenPunkt><MetaFTAgendaItem><ItemNo>0</ItemNo><FTCase /><FTCaseNumber /><FTCaseType>FM</FTCaseType>

In [ ]:
response = urllib.request.urlopen(url)

In [ ]:
data = response.read()

In [ ]:
from bs4 import BeautifulSoup
soup = BeautifulSoup(data, 'html.parser')

In [ ]:
print(soup.decode())

In [ ]:
data

In [20]:
final_data = pd.DataFrame()
for i in range(10):
    
    url = "https://itunes.apple.com/us/rss/customerreviews/page={}/id=284882215/sortBy=mostrecent/xml".format(i+1)
    
    xml_data = requests.get(url).content

    soup = bs(xml_data, "xml")
     
    # Find all text in the data
    texts = str(soup.findAll(text=True)).replace('\\n','')
    
    #Find the tag/child
    child = soup.find("entry")
    
    Title = []
    content_type = []
    updated = []
    rating = []
    user_name = []
    
    while True:    
        try:
            updated.append(" ".join(child.find('updated')))
        except:
            updated.append(" ")
            
        try:
            Title.append(" ".join(child.find('title')))
        except:
            Title.append(" ")
        
        try:
            content_type.append(" ".join(child.find('content')))
        except:
            content_type.append(" ")
            
        try:
            rating.append(" ".join(child.find('im:rating')))
        except:
            rating.append(" ")
        
        try:
            user_name.append(" ".join(child.find('name')))
        except:
            user_name.append(" ")
        
        try:   
            # Next sibling of child, here: entry 
            child = child.find_next_sibling('entry')
        except:
            break
    
    data = []
    data = pd.DataFrame({"updated":updated,
                                    "Title":Title,
                                    "content_type":content_type,
                                    "rating":rating,
                                    "user_name":user_name})
    final_data = final_data.append(data, ignore_index = True)


In [21]:
final_data

updated  \
0    2020-11-30T12:19:49-07:00   
1    2020-11-30T12:14:07-07:00   
2    2020-11-30T12:11:11-07:00   
3    2020-11-30T12:03:46-07:00   
4    2020-11-30T12:01:44-07:00   
..                         ...   
505  2020-11-28T10:46:21-07:00   
506  2020-11-28T10:45:26-07:00   
507  2020-11-28T10:43:57-07:00   
508  2020-11-28T10:27:11-07:00   
509                              

                                                 Title  \
0    Your censorship of conservative POV’s is abhor...   
1                         Hate how the emojis look now   
2                                Election interference   
3                                               Review   
4                      Far left leaning administrators   
..                                                 ...   
505                             Facebook is ridiculous   
506                                    Disable account   
507                                  I LOST EVERYTHING   
508                                 Socialist platform   
509                                                      

                                          content_type rating  \
0                                                 Boo!      1   
1    Every since they updated the app, my emojis ha...      2   
2    I hate that Facebook had to interfere in our A...      1   
3    As an intelligent member of society, I joined ...      1   
4    Their “Fact Checkers” go way out of their way ...      1   
..                                                 ...    ...   
505  Tired of the censorship. Would have given 0 bu...      1   
506  I don’t know what is happening with Facebook i...      1   
507  I am 23 and Facebook randomly deemed I was not...      1   
508  Sick of being censored, soon to cancel Faceboo...      1   
509                                                             

             user_name  
0          Marsthon315  
1              ShakKay  
2           Krhea46012  
3          Wildman1369  
4               TClyse  
..                 ...  
505           Nick7262  
506         pandidbd f  
507  bluerocketporkham  
508           2020 ann  
509                     

[510 rows x 5 columns]

In [ ]:
stopwords = open('stopord.txt').read().splitlines() #Link: https://gist.github.com/berteltorp/0cf8a0c7afea7f25ed754f24cfc2467b

In [ ]:
# convert the text to a tf-idf weighted term-document matrix

# Hyperparameters
corpus = 2000000 #Der er ca. ? forskellige ord, efter stopord
l1_ratio = 0
max_iter = 50000
no_components = 30

min_df = 2
max_df = 0.6


vectorizer = TfidfVectorizer(max_features=corpus, min_df=min_df, max_df=max_df, stop_words=stopwords)

X = vectorizer.fit_transform(data)
 
idx_to_word = np.array(vectorizer.get_feature_names())


# apply NMF
nmf = NMF(n_components=no_components, solver="mu", l1_ratio = l1_ratio, max_iter = max_iter, random_state=1)

W = nmf.fit_transform(X)

H = nmf.components_
 
# print the topics
 
for i, topic in enumerate(H):
 
    print("Topic {}: {}".format(i + 1, ", ".join([str(x) for x in idx_to_word[topic.argsort()[-10:]]])))

In [ ]:
# Write to a .csv file
import csv
with open('topics_and_weights.csv', 'w', newline='', encoding='utf-16') as csvfile:
    topicwriter = csv.writer(csvfile, delimiter=',',
                            quotechar='"', quoting=csv.QUOTE_MINIMAL)
# Create the header
    topicwriter.writerow(['Topic','Word','Weight'])

In [ ]:
# print the topics for tableau
 
for i, topic in enumerate(H):
 
    max_weights = topic.argsort()[-10:]
    words = [str(x) for x in idx_to_word[topic.argsort()[-10:]]]
     
    for count, item in enumerate(max_weights):
        
        with open('topics_and_weights.csv', 'a', newline='', encoding='utf-16') as csvfile:
            topicwriter = csv.writer(csvfile, delimiter=',',
                            quotechar='"', quoting=csv.QUOTE_MINIMAL)
            topicwriter.writerow(["Topic"+str(i+1) ,words[count],H[i,item]])

In [ ]:
#stopwords_edit = open('stopord.txt','a')
#stopwords_edit.write('\nenhedslisten')
#stopwords_edit.close()